In [19]:
import requests  
import pandas as pd  

# Replace 'YOUR_API_KEY' with the actual key  
api_url = "https://api.data.gov.in/resource/35985678-0d79-46b4-9ed6-6f13308a1d24?api-key=579b464db66ec23bdd00000127fb7fc240a84d565d77daff0d1ed4d1&format=json&limit=1000"

response = requests.get(api_url)  
data = response.json()  

# Convert JSON to DataFrame  
df = pd.DataFrame(data["records"])  

# Save as CSV  
df.to_csv("agmarknet_data1.csv", index=False)  
print("Data saved successfully!")


Data saved successfully!


In [17]:
import requests  
import json  

# Replace 'YOUR_API_KEY' and 'YOUR_RESOURCE_ID' with actual values  
api_url = "https://api.data.gov.in/resource/35985678-0d79-46b4-9ed6-6f13308a1d24?api-key=579b464db66ec23bdd00000127fb7fc240a84d565d77daff0d1ed4d1&format=json&limit=1000"

response = requests.get(api_url)  
data = response.json()  

# Print the full response to inspect its structure  
print(json.dumps(data, indent=4))  


{
    "index_name": "35985678-0d79-46b4-9ed6-6f13308a1d24",
    "title": "Variety-wise Daily Market Prices Data of Commodity",
    "desc": "Variety-wise Daily Market Prices Data of Commodity",
    "org_type": "Central",
    "org": [
        "Ministry of Agriculture and Farmers Welfare",
        "Department of Agriculture and Farmers Welfare",
        "Directorate of Marketing and Inspection (DMI)"
    ],
    "sector": [
        "Agriculture",
        "Agricultural Marketing"
    ],
    "source": "data.gov.in",
    "catalog_uuid": "6141ea17-a69d-4713-b600-0a43c8fd9a6c",
    "visualizable": "0",
    "active": "1",
    "created": 1695098583,
    "updated": 1739234152,
    "created_date": "2023-09-19T06:43:03Z",
    "updated_date": "2025-02-11T00:35:52Z",
    "external_ws": 0,
    "external_ws_url": "",
    "target_bucket": {
        "index": "agmarknet",
        "type": "6141ea17-a69d-4713-b600-0a43c8fd9a6c",
        "field": "35985678-0d79-46b4-9ed6-6f13308a1d24"
    },
    "field": [
  

import requests
import pandas as pd
import time

# Replace with your actual API key and resource ID
API_KEY = "579b464db66ec23bdd00000127fb7fc240a84d565d77daff0d1ed4d1"
RESOURCE_ID = "35985678-0d79-46b4-9ed6-6f13308a1d24"
BASE_URL = f"https://api.data.gov.in/resource/{RESOURCE_ID}?api-key={API_KEY}&format=json"

LIMIT = 1000  # API limit per request
offset = 0    # Start from first record
all_data = [] # Store all records

while True:
    # Construct URL with pagination
    api_url = f"{BASE_URL}&limit={LIMIT}&offset={offset}"
    
    # Fetch data
    response = requests.get(api_url)
    
    if response.status_code == 200:
        data = response.json()
        records = data.get("records", [])
        
        if not records:
            break  # Stop if no more data
        
        all_data.extend(records)  # Add new records
        offset += LIMIT  # Move to next batch
        time.sleep(1)  # Avoid excessive requests
    
    else:
        print(f"Error {response.status_code}: {response.text}")
        break  # Stop if API request fails

# Convert to DataFrame and save
df = pd.DataFrame(all_data)
df.to_csv("agmarknet_data.csv", index=False)
print(f"Total records fetched: {len(df)}")


In [32]:
import requests
import pandas as pd

def get_weather_data(lat, lon, state_name, file_name):
    """Fetch historical weather data for a given location using NASA POWER API and store it in a CSV file."""
    url = f"https://power.larc.nasa.gov/api/temporal/daily/point?parameters=T2M,PRECTOTCORR,RH2M&start=20190101&end=20250131&latitude={lat}&longitude={lon}&community=AG&format=JSON"

    response = requests.get(url)
    
    try:
        data = response.json()
        print(f"🔹 API Response for {state_name}: {data}")  # Debugging line

        if "properties" not in data or "parameter" not in data["properties"]:
            print(f"⚠️ No 'properties' or 'parameter' key in response for {state_name}.")
            return None

        params = data["properties"]["parameter"]

        # Check for 'PRECTOTCORR' in response
        if "PRECTOTCORR" not in params:
            print(f"⚠️ 'PRECTOTCORR' (corrected rainfall) not found in the API response for {state_name}.")
            return None  

        # Extract required data
        dates = list(params["T2M"].keys())  # Temperature
        temp = list(params["T2M"].values())
        rainfall = list(params["PRECTOTCORR"].values())  # Corrected Rainfall
        humidity = list(params["RH2M"].values())  # Humidity

        # Create DataFrame
        df = pd.DataFrame({"Date": dates, "Temperature": temp, "Rainfall": rainfall, "Humidity": humidity})
        df["State"] = state_name

        # Save DataFrame to CSV
        df.to_csv(file_name, index=False)
        print(f"✅ Data for {state_name} saved to {file_name}")

        return df

    except Exception as e:
        print(f"❌ Error fetching data for {state_name}: {e}")
        return None

# Test with a single location (Maharashtra)
df_test = get_weather_data(19.7515, 75.7139, "Maharashtra", "maharashtra_weather_data.csv")

if df_test is not None:
    print(df_test.tail())  # Show the last few records to see if data for 2024 is included
else:
    print("⚠️ No data received.")


🔹 API Response for Maharashtra: {'header': 'The POWER Daily API failed to complete your request; please review the errors below and the POWER Docs (https://power.larc.nasa.gov/docs/).', 'messages': ['Please provide a correct end date formatting.']}
⚠️ No 'properties' or 'parameter' key in response for Maharashtra.
⚠️ No data received.


In [36]:
import requests
import pandas as pd

def get_weather_data(lat, lon, state_name, file_name):
    """Fetch historical weather data for a given location using NASA POWER API and store it in a CSV file."""
    url = f"https://power.larc.nasa.gov/api/temporal/daily/point?parameters=T2M,PRECTOTCORR,RH2M&start=20190101&end=20250131&latitude={lat}&longitude={lon}&community=AG&format=JSON"

    response = requests.get(url)
    
    try:
        data = response.json()
        print(f"🔹 API Response for {state_name}: {data}")  # Debugging line

        if "properties" not in data or "parameter" not in data["properties"]:
            print(f"⚠️ No 'properties' or 'parameter' key in response for {state_name}.")
            return None

        params = data["properties"]["parameter"]

        # Check for 'PRECTOTCORR' in response
        if "PRECTOTCORR" not in params:
            print(f"⚠️ 'PRECTOTCORR' (corrected rainfall) not found in the API response for {state_name}.")
            return None  

        # Extract required data
        dates = list(params["T2M"].keys())  # Temperature
        temp = list(params["T2M"].values())
        rainfall = list(params["PRECTOTCORR"].values())  # Corrected Rainfall
        humidity = list(params["RH2M"].values())  # Humidity

        # Create DataFrame
        df = pd.DataFrame({"Date": dates, "Temperature": temp, "Rainfall": rainfall, "Humidity": humidity})
        df["State"] = state_name

        # Save DataFrame to CSV
        df.to_csv(file_name, index=False)
        print(f"✅ Data for {state_name} saved to {file_name}")

        return df

    except Exception as e:
        print(f"❌ Error fetching data for {state_name}: {e}")
        return None

# Coordinates for the states
state_coords = {
    "Odisha": (20.9517, 85.0985),
    "Madhya Pradesh": (22.9734, 78.6569),
    "Assam": (26.2006, 92.9376),
    "Haryana": (29.0588, 76.0856),
    "Kerala": (10.8505, 76.2711),
    "Tamil Nadu": (11.1271, 78.6569),
    "West Bengal": (22.9868, 87.8550),
    "Himachal Pradesh": (31.1048, 77.1734),
    "Telangana": (18.1124, 79.0193),
    "Bihar": (25.0961, 85.3131),
    "Andhra Pradesh": (15.9129, 79.7400),
    "Chattisgarh": (21.2787, 81.8661),
    "Karnataka": (15.3173, 75.7139),
    "Goa": (15.2993, 74.1240),
    "Maharashtra": (19.7515, 75.7139),
    "Punjab": (31.1471, 75.3412),
    "Jammu and Kashmir": (33.7782, 76.5762),
    "Meghalaya": (25.4670, 91.3662),
    "Manipur": (24.6637, 93.9063),
    "NCT of Delhi": (28.7041, 77.1025),
    "Rajasthan": (27.0238, 74.2179),
    "Uttrakhand": (30.0668, 79.0193),
    "Nagaland": (26.1584, 94.5624),
    "Jharkhand": (23.6102, 85.2799),
    "Uttar Pradesh": (26.8467, 80.9462),
    "Gujarat": (22.2587, 71.1924),
    "Tripura": (23.9408, 91.9882),
    "Andaman and Nicobar": (11.7401, 92.6586),
    "Mizoram": (23.1645, 92.9376),
    "Chandigarh": (30.7333, 76.7794)
}

all_data = pd.DataFrame()

# Fetch data for all states and store it in a single DataFrame
for state, coords in state_coords.items():
    lat, lon = coords
    df = get_weather_data(lat, lon, state)
    if df is not None:
        all_data = pd.concat([all_data, df], ignore_index=True)
    else:
        print(f"⚠️ No data received for {state}.")

# Save the combined DataFrame to a single CSV file
all_data.to_csv("all_states_weather_data.csv", index=False)
print("✅ All data saved to all_states_weather_data.csv")

# Show the last few records to see if data for 2024 is included
print(all_data.tail())


TypeError: get_weather_data() missing 1 required positional argument: 'file_name'

In [38]:
import requests
import pandas as pd

def get_weather_data(lat, lon, state_name):
    """Fetch historical weather data for a given location using NASA POWER API."""
    url = f"https://power.larc.nasa.gov/api/temporal/daily/point?parameters=T2M,PRECTOTCORR,RH2M&start=20190101&end=20250131&latitude={lat}&longitude={lon}&community=AG&format=JSON"

    response = requests.get(url)
    
    try:
        data = response.json()
        print(f"🔹 API Response for {state_name}: {data}")  # Debugging line

        if "properties" not in data or "parameter" not in data["properties"]:
            print(f"⚠️ No 'properties' or 'parameter' key in response for {state_name}.")
            return None

        params = data["properties"]["parameter"]

        # Check for 'PRECTOTCORR' in response
        if "PRECTOTCORR" not in params:
            print(f"⚠️ 'PRECTOTCORR' (corrected rainfall) not found in the API response for {state_name}.")
            return None  

        # Extract required data
        dates = list(params["T2M"].keys())  # Temperature
        temp = list(params["T2M"].values())
        rainfall = list(params["PRECTOTCORR"].values())  # Corrected Rainfall
        humidity = list(params["RH2M"].values())  # Humidity

        # Create DataFrame
        df = pd.DataFrame({"Date": dates, "Temperature": temp, "Rainfall": rainfall, "Humidity": humidity})
        df["State"] = state_name

        return df

    except Exception as e:
        print(f"❌ Error fetching data for {state_name}: {e}")
        return None

# Coordinates for the states
state_coords = {
    "Odisha": (20.9517, 85.0985),
    "Madhya Pradesh": (22.9734, 78.6569),
    "Assam": (26.2006, 92.9376),
    "Haryana": (29.0588, 76.0856),
    "Kerala": (10.8505, 76.2711),
    "Tamil Nadu": (11.1271, 78.6569),
    "West Bengal": (22.9868, 87.8550),
    "Himachal Pradesh": (31.1048, 77.1734),
    "Telangana": (18.1124, 79.0193),
    "Bihar": (25.0961, 85.3131),
    "Andhra Pradesh": (15.9129, 79.7400),
    "Chattisgarh": (21.2787, 81.8661),
    "Karnataka": (15.3173, 75.7139),
    "Goa": (15.2993, 74.1240),
    "Maharashtra": (19.7515, 75.7139),
    "Punjab": (31.1471, 75.3412),
    "Jammu and Kashmir": (33.7782, 76.5762),
    "Meghalaya": (25.4670, 91.3662),
    "Manipur": (24.6637, 93.9063),
    "NCT of Delhi": (28.7041, 77.1025),
    "Rajasthan": (27.0238, 74.2179),
    "Uttrakhand": (30.0668, 79.0193),
    "Nagaland": (26.1584, 94.5624),
    "Jharkhand": (23.6102, 85.2799),
    "Uttar Pradesh": (26.8467, 80.9462),
    "Gujarat": (22.2587, 71.1924),
    "Tripura": (23.9408, 91.9882),
    "Andaman and Nicobar": (11.7401, 92.6586),
    "Mizoram": (23.1645, 92.9376),
    "Chandigarh": (30.7333, 76.7794)
}

# Initialize an empty DataFrame to store all data
all_data = pd.DataFrame()

# Fetch data for all states and store it in a single DataFrame
for state, coords in state_coords.items():
    lat, lon = coords
    df = get_weather_data(lat, lon, state)
    if df is not None:
        all_data = pd.concat([all_data, df], ignore_index=True)
    else:
        print(f"⚠️ No data received for {state}.")

# Save the combined DataFrame to a single CSV file
all_data.to_csv("all_states_weather_data.csv", index=False)
print("✅ All data saved to all_states_weather_data.csv")

# Show the last few records to see if data for 2024 is included
print(all_data.tail())


🔹 API Response for Odisha: {'type': 'Feature', 'geometry': {'type': 'Point', 'coordinates': [85.099, 20.952, 206.61]}, 'properties': {'parameter': {'T2M': {'20190101': 14.99, '20190102': 15.84, '20190103': 15.85, '20190104': 16.4, '20190105': 17.04, '20190106': 17.45, '20190107': 18.33, '20190108': 16.33, '20190109': 16.6, '20190110': 17.4, '20190111': 16.57, '20190112': 17.18, '20190113': 18.21, '20190114': 18.03, '20190115': 17.8, '20190116': 17.12, '20190117': 17.67, '20190118': 17.92, '20190119': 17.92, '20190120': 18.44, '20190121': 19.17, '20190122': 19.1, '20190123': 19.53, '20190124': 20.12, '20190125': 19.6, '20190126': 19.18, '20190127': 18.17, '20190128': 19.34, '20190129': 18.15, '20190130': 16.69, '20190131': 17.88, '20190201': 18.99, '20190202': 20.35, '20190203': 21.09, '20190204': 20.89, '20190205': 20.59, '20190206': 22.18, '20190207': 22.65, '20190208': 22.83, '20190209': 21.6, '20190210': 18.77, '20190211': 19.37, '20190212': 20.52, '20190213': 21.63, '20190214': 22.